In [1]:
from ngsolve import *
from ngsolve.webgui import Draw
from netgen.occ import *
from ngsolve.meshes import MakeStructured2DMesh

In [2]:
L = 1
L_1 = 1
mesh = MakeStructured2DMesh(quads=False, nx=50,ny=50, mapping= lambda x,y : (L*(x),L_1*(y)))

# mesh = Mesh (unit_square.GenerateMesh(maxh=0.1))
Draw(mesh)
mesh.GetBoundaries()

WebGuiWidget(layout=Layout(height='50vh', width='100%'), value={'gui_settings': {}, 'ngsolve_version': '6.2.23…

('bottom', 'right', 'top', 'left')

In [3]:
q = -200

In [4]:
V = HDivDiv(mesh, order=1, dirichlet= "")
Q = H1(mesh, order=2, dirichlet="left|right|top|bottom")
X = V*Q
(sigma, w), (tau, v) = X.TnT()

n = specialcf.normal(2)

def tang(u): return u-(u*n)*n

a = BilinearForm(X, symmetric=True)
a += (InnerProduct(sigma, tau) + div(sigma)*grad(v) \
          + div(tau)*grad(w) )*dx \
          + (-(sigma*n) * tang(grad(v)) - (tau*n)*tang(grad(w)))*dx(element_boundary=True)
a.Assemble()

f = LinearForm(X)
f += q*v*dx
f.Assemble()

gfsol = GridFunction(X)
gfsol.vec.data = a.mat.Inverse(X.FreeDofs(), inverse="sparsecholesky") * f.vec

In [5]:
gfsigma, gfw = gfsol.components

In [6]:
 Draw(gfw, mesh, name="disp", deformation=True)

WebGuiWidget(layout=Layout(height='50vh', width='100%'), value={'gui_settings': {}, 'ngsolve_version': '6.2.23…

BaseWebGuiScene